In [0]:
spark.conf.set(
    "fs.azure.account.key.netflixdatalakes.dfs.core.windows.net",
    dbutils.secrets.get(scope="mysecrets", key="netflix_key")
)


In [0]:
from pyspark.sql.functions import *
from pyspark.sql.types import *
from pyspark.sql.window import Window

In [0]:
df = spark.read.format("delta")\
    .load("abfss://silver@netflixdatalakes.dfs.core.windows.net/netflix_titles_for_gold")


In [0]:
df_cast = spark.read.format("delta")\
    .load("abfss://silver@netflixdatalakes.dfs.core.windows.net/netflix_cast")

df_category = spark.read.format("delta")\
    .load("abfss://silver@netflixdatalakes.dfs.core.windows.net/netflix_category")

df_countries = spark.read.format("delta")\
    .load("abfss://silver@netflixdatalakes.dfs.core.windows.net/netflix_countries")

df_directors= spark.read.format("delta")\
    .load("abfss://silver@netflixdatalakes.dfs.core.windows.net/netflix_directors")

In [0]:
df_cast.limit(10).show()

+----------------+--------+
|            cast| show_id|
+----------------+--------+
|   Alan Marriott|81145628|
|Jandino Asporaat|80117401|
|    Peter Cullen|70234439|
|    Will Friedle|80058654|
|    Nesta Cooper|80125979|
|  Alberto Ammann|80163890|
|Antonio Banderas|70304989|
| Fabrizio Copano|80164077|
|    James Franco|70304990|
|   Joaquín Reyes|80169755|
+----------------+--------+



In [0]:
df_category.limit(10).show()

+--------------------+--------+
|           listed_in| show_id|
+--------------------+--------+
|Children & Family...|81145628|
|     Stand-Up Comedy|80117401|
|            Kids' TV|70234439|
|            Kids' TV|80058654|
|            Comedies|80125979|
|      Crime TV Shows|80163890|
|International Movies|70304989|
|     Stand-Up Comedy|80164077|
|          Docuseries|80117902|
|  Action & Adventure|70304990|
+--------------------+--------+



In [0]:
df_countries.limit(10).show()


+--------------+--------+
|       country| show_id|
+--------------+--------+
|       Germany|80016401|
|  South Africa|80182274|
| United States|80182274|
| United States|81145628|
|United Kingdom|80117401|
| United States|70234439|
| United States|80058654|
| United States|80125979|
|         Spain|80163890|
|      Bulgaria|70304989|
+--------------+--------+



In [0]:
df_directors.limit(10).show()

+--------------------+--------+
|            director| show_id|
+--------------------+--------+
|        Richard Finn|81145628|
|    Fernando Lebrija|80125979|
|         Gabe Ibáñez|70304989|
|        Rodrigo Toro|80164077|
|   Henrik Ruben Genz|70304990|
|José Miguel Contr...|80169755|
|    Daniel Alfredson|70299204|
|       Munjal Shroff|80182483|
|       Munjal Shroff|80182596|
|        Tilak Shetty|80182482|
+--------------------+--------+



In [0]:
df.limit(10).show()

+----------------+----------------+-----+--------------------+----------+------------+------+--------------------+--------+--------------------+---------+----------------+
|duration_minutes|duration_seasons| type|               title|date_added|release_year|rating|         description| show_id|         Short_title|type_flag|duration_ranking|
+----------------+----------------+-----+--------------------+----------+------------+------+--------------------+--------+--------------------+---------+----------------+
|             312|               1|Movie|Black Mirror: Ban...|12/28/2018|        2018|    TV|In 1984, a young ...|80988062|        Black Mirror|        1|               1|
|             228|               1|Movie|              Sangam|12/31/2019|        1964|    TV|Returning home fr...|60002818|              Sangam|        1|               2|
|             224|               1|Movie|              Lagaan| 12/8/2017|        2001|    PG|In 1890s India, a...|60020906|              Lag

In [0]:

# 3. Add analytical flags
df_flags = df.withColumn("is_family_friendly", when(col("rating").isin("G", "PG", "TV-G", "TV-Y", "TV-Y7"), 1).otherwise(0))

In [0]:
df_flags.limit(10).show()

+----------------+----------------+-----+--------------------+----------+------------+------+--------------------+--------+--------------------+---------+----------------+------------------+
|duration_minutes|duration_seasons| type|               title|date_added|release_year|rating|         description| show_id|         Short_title|type_flag|duration_ranking|is_family_friendly|
+----------------+----------------+-----+--------------------+----------+------------+------+--------------------+--------+--------------------+---------+----------------+------------------+
|             312|               1|Movie|Black Mirror: Ban...|12/28/2018|        2018|    TV|In 1984, a young ...|80988062|        Black Mirror|        1|               1|                 0|
|             228|               1|Movie|              Sangam|12/31/2019|        1964|    TV|Returning home fr...|60002818|              Sangam|        1|               2|                 0|
|             224|               1|Movie|    

Movies with screen time less than 90 min.

In [0]:
df_lessthan_90 = df_flags.filter((col("duration_minutes") < 90) & (col("type") == "Movie"))
df_lessthan_90.limit(10).show()

+----------------+----------------+-----+--------------------+----------+------------+------+--------------------+--------+--------------------+---------+----------------+------------------+
|duration_minutes|duration_seasons| type|               title|date_added|release_year|rating|         description| show_id|         Short_title|type_flag|duration_ranking|is_family_friendly|
+----------------+----------------+-----+--------------------+----------+------------+------+--------------------+--------+--------------------+---------+----------------+------------------+
|              89|               1|Movie|              Domino| 9/28/2019|        2019|     R|A Copenhagen poli...|80200087|              Domino|        1|             111|                 0|
|              89|               1|Movie|               Leap!| 9/25/2019|        2016|    PG|Félicie and Victo...|80166318|               Leap!|        1|             111|                 1|
|              89|               1|Movie|    

Movies from Director Rodrigo Toro

In [0]:
df_flags.groupBy('show_id').count().filter("count>1").show()



+--------+-----+
| show_id|count|
+--------+-----+
|70114043|    2|
|80113667|    2|
|80017099|    2|
|80190449|    2|
|80117533|    2|
|81067757|    2|
|70117902|    2|
|80144453|    2|
|81074367|    2|
|80105691|    2|
|80195964|    2|
|80134520|    2|
|80174220|    2|
|80133139|    2|
|80144141|    2|
|81034010|    2|
|80189653|    2|
|80158875|    2|
|80182622|    2|
|81096745|    2|
+--------+-----+
only showing top 20 rows



In [0]:
df_flags= df_flags.dropDuplicates(['show_id'])
df_flags.groupBy('show_id').count().filter("count>1").show()

+-------+-----+
|show_id|count|
+-------+-----+
+-------+-----+



In [0]:
df_directors.groupBy('show_id').count().filter("count>1").show()

+--------+-----+
| show_id|count|
+--------+-----+
|80198423|    3|
|80144152|    3|
|22497725|    3|
|70123120|    3|
|80165848|    3|
|70308135|    3|
|80238080|    3|
|80039136|    3|
|80144311|    3|
|80993655|    3|
|81033473|    3|
|80016588|    3|
|80208661|    3|
|80154179|    3|
|80185876|    3|
|81213884|    3|
|70113636|    3|
|70043379|    6|
|70077546|    3|
|80094648|    3|
+--------+-----+
only showing top 20 rows



In [0]:
df_directors= df_directors.dropDuplicates(['show_id'])
df_directors.groupBy('show_id').count().filter("count>1").show()

+-------+-----+
|show_id|count|
+-------+-----+
+-------+-----+



In [0]:
director_grouped = df_directors.groupBy("show_id").agg(
    collect_list("director").alias("director_list")
)

df_enriched = df_flags.join(director_grouped, on="show_id", how="left")

df_enriched.limit(10).show()

+--------+----------------+----------------+-----+--------------------+----------+------------+------+--------------------+--------------------+---------+----------------+------------------+--------------------+
| show_id|duration_minutes|duration_seasons| type|               title|date_added|release_year|rating|         description|         Short_title|type_flag|duration_ranking|is_family_friendly|       director_list|
+--------+----------------+----------------+-----+--------------------+----------+------------+------+--------------------+--------------------+---------+----------------+------------------+--------------------+
|60002818|             228|               1|Movie|              Sangam|12/31/2019|        1964|    TV|Returning home fr...|              Sangam|        1|               2|                 0|[Raj Kapoor, Raj ...|
|60020906|             224|               1|Movie|              Lagaan| 12/8/2017|        2001|    PG|In 1890s India, a...|              Lagaan|        

In [0]:


df_enriched.filter(array_contains(col("director_list"), "Rodrigo Toro")).limit(10).show()


show_id duration_minutes duration_seasons type title date_added release_year rating description Short_title type_flag duration_ranking is_family_friendly director_list 80164077 60 1 Movie Fabrizio Copano: Solo pienso en mi 9/8/2017 2017 TV Fabrizio Copano takes audience participation to the next level in this stand-up set while reflecting on sperm banks, family WhatsApp groups and more. Fabrizio Copano 1 140 0 List(Rodrigo Toro)

Movies released before 2018

In [0]:
df_before_2018 = df_flags.filter(col('release_year') < 2018)
df_before_2018.select('Short_title','release_year').limit(10).show()

+--------------------+------------+
|         Short_title|release_year|
+--------------------+------------+
|              Sangam|        1964|
|              Lagaan|        2001|
|        Jodhaa Akbar|        2008|
|  The Gospel of Luke|        2015|
|What's Your Raashee?|        2009|
|The Lord of the R...|        2003|
|      Doctor Zhivago|        1965|
|Elephants Dream 4...|        2006|
|    Schindler's List|        1993|
| Hum Aapke Hain Koun|        1994|
+--------------------+------------+



Movies by cast Kareena Kapoor and Amir Khan together

In [0]:
df_cast.groupBy('show_id').count().filter('count>1').limit(10).show()

+--------+-----+
| show_id|count|
+--------+-----+
|70143865|    4|
|80144152|    8|
|22497725|   10|
|70123120|    8|
|80165848|    7|
|70308135|   10|
|80238080|   10|
|80172475|    3|
|80039136|    8|
|80144311|    6|
+--------+-----+



In [0]:
cast_grouped = df_cast.groupBy("show_id").agg(
    collect_list("cast").alias("cast_list")
)

df_casted = df_flags.join(cast_grouped, on="show_id", how="inner")

df_casted.limit(10).show()

+--------+----------------+----------------+-----+--------------------+----------+------------+------+--------------------+--------------------+---------+----------------+------------------+--------------------+
| show_id|duration_minutes|duration_seasons| type|               title|date_added|release_year|rating|         description|         Short_title|type_flag|duration_ranking|is_family_friendly|           cast_list|
+--------+----------------+----------------+-----+--------------------+----------+------------+------+--------------------+--------------------+---------+----------------+------------------+--------------------+
|80988062|             312|               1|Movie|Black Mirror: Ban...|12/28/2018|        2018|    TV|In 1984, a young ...|        Black Mirror|        1|               1|                 0|[Fionn Whitehead,...|
|60002818|             228|               1|Movie|              Sangam|12/31/2019|        1964|    TV|Returning home fr...|              Sangam|        

In [0]:
df_casted.groupBy('show_id').count().filter('count>1').display()

show_id count

In [0]:
df_casted.filter(col('show_id')=='81074367').display()

show_id duration_minutes duration_seasons type title date_added release_year rating description Short_title type_flag duration_ranking is_family_friendly cast_list 81074367 107 1 Movie Jaoon Kahan Bata Ae Dil 8/9/2019 2018 TV A couple’s caustic, increasingly jarring interactions over a Mumbai evening strain their relationship until it threatens to break at its fraying seams. Jaoon Kahan Bata Ae Dil 1 93 0 List(Khushboo Upadhyay, Rohit Kokate, Himanshu Kohli, Mohammed Shakir)

In [0]:
df_casted= df_casted.dropDuplicates(['show_id'])

In [0]:
df_casted.filter(col('show_id')=='81074367').display()

show_id duration_minutes duration_seasons type title date_added release_year rating description Short_title type_flag duration_ranking is_family_friendly cast_list 81074367 107 1 Movie Jaoon Kahan Bata Ae Dil 8/9/2019 2018 TV A couple’s caustic, increasingly jarring interactions over a Mumbai evening strain their relationship until it threatens to break at its fraying seams. Jaoon Kahan Bata Ae Dil 1 93 0 List(Khushboo Upadhyay, Rohit Kokate, Himanshu Kohli, Mohammed Shakir)

In [0]:
df_kareena = df_casted.filter(array_contains(col("cast_list"), "Kareena Kapoor") & array_contains(col("cast_list"), "Aamir Khan"))
df_kareena.display()

show_id duration_minutes duration_seasons type title date_added release_year rating description Short_title type_flag duration_ranking is_family_friendly cast_list 70121522 164 1 Movie 3 Idiots 8/1/2019 2009 PG While attending one of India's premier colleges, three miserable engineering students and best friends struggle to beat the school's draconian system. 3 Idiots 1 36 1 List(Aamir Khan, Omi Vaidya, Mona Singh, Boman Irani, Kareena Kapoor, Madhavan, Sharman Joshi, Javed Jaffrey) 70262614 140 1 Movie Talaash 12/15/2019 2012 TV Set in the jumbled landscape of Mumbai, this mystery drama centers on a police inspector who's trying to cope with the collapse of his marriage. Talaash 1 60 0 List(Aamir Khan, Shernaz Patel, Sheeba Chaddha, Rani Mukerji, Kareena Kapoor, Nawazuddin Siddiqui)

> Total number of movie count in year 2018, 2019, 2020

In [0]:
df_overtheyears = df_flags.filter((col('type')=='Movie') & (col('release_year').isin(['2018','2019','2020'])))
df_overtheyears.display()

duration_minutes duration_seasons type title date_added release_year rating description show_id Short_title type_flag duration_ranking is_family_friendly 107 1 Movie Jaoon Kahan Bata Ae Dil 8/9/2019 2018 TV A couple’s caustic, increasingly jarring interactions over a Mumbai evening strain their relationship until it threatens to break at its fraying seams. 81074367 Jaoon Kahan Bata Ae Dil 1 93 0 100 1 Movie Anon 5/4/2018 2018 TV In a future where technology has rendered privacy obsolete, a detective investigates a serial assassin who has been deleted from all visual records. 80195964 Anon 1 100 0 84 1 Movie Back to School 8/30/2019 2019 TV Eager to flaunt their success in front of old bullies and teenage crushes, two best friends spend a wild night at their middle school reunion. 81034010 Back to School 1 116 0 79 1 Movie Ricky Gervais: Humanity 3/13/2018 2018 TV In his first special in seven years, Ricky Gervais slings his trademark snark at celebrity, mortality and a society that takes everything personally. 80189653 Ricky Gervais 1 121 0 66 1 Movie Greg Davies: You Magnificent Beast 4/10/2018 2018 TV British comedian Greg Davies revisits terrifying dates, manscaping disasters, his father's pranks and more in a savagely funny stand-up special. 80158875 Greg Davies 1 134 0 54 1 Movie Fadily Camara : La plus drôle de tes copines 11/14/2019 2019 TV Irrepressible French comedian Fadily Camara weaves jokes, vivid characters and physical comedy into a lively stand-up show at La Cigale in Paris. 81096745 Fadily Camara 1 146 0 122 1 Movie The Edge of Democracy 6/19/2019 2019 TV Political documentary and personal memoir collide in this exploration into the complex truth behind the unraveling of two Brazilian presidencies. 80190535 The Edge of Democracy 1 78 0 114 1 Movie The Great Hack 7/24/2019 2019 TV Explore how a data company named Cambridge Analytica came to symbolize the dark side of social media in the wake of the 2016 U.S. presidential election. 80117542 The Great Hack 1 86 0 100 1 Movie On My Skin 9/12/2018 2018 TV Arrested in Rome for a drug-related offense, Stefano Cucchi endures a harrowing week in custody that changes his family forever. Based on true events. 81001000 On My Skin 1 100 0 71 1 Movie Pachamama 6/7/2019 2019 PG When a sacred statue is taken from his Andean village, a spirited boy who dreams of becoming a shaman goes on a brave mission to get it back. 81029736 Pachamama 1 129 1 66 1 Movie Once In A Lifetime Sessions with Noel Gallagher 8/1/2018 2018 TV Between scenes from an intimate performance, the Oasis legend reflects on his road to stardom and offers insights on his creative process. 81001382 Once In A Lifetime Sessions with Noel Gallagher 1 134 0 132 1 Movie Di Renjie zhi Sidatianwang 2/6/2019 2018 TV Framed by an empress who plans to steal a dragon-taming mace, imperial magistrate Dee Renjie soon uncovers a greater plot that threatens the kingdom. 81010962 Di Renjie zhi Sidatianwang 1 68 0 88 1 Movie Only Mine 1/15/2019 2018 TV After dating a charming cop who turns into an obsessive stalker, a small-town girl must save herself from his deadly ways. 81050191 Only Mine 1 112 0 61 1 Movie Francesco De Carlo: Cose di Questo Mondo 4/12/2019 2019 TV Taking the stage in Milan, Francesco De Carlo opens up about his bad habits, religion, politics and what he's learned from traveling the world. 81041272 Francesco De Carlo 1 139 0 94 1 Movie Zoo 7/1/2018 2018 TV A drug dealer starts having doubts about his trade as his brother, his client, and two rappers from the slums each battle their own secret addictions. 80993648 Zoo 1 106 0 117 1 Movie Catching Feelings 5/18/2018 2018 TV Amid growing tensions in their marriage, a Johannesburg professor and his journalist wife find their lives upended by a famous, hard-partying author. 80218111 Catching Feelings 1 83 0 97 1 Movie Dude 4/20/2018 2018 TV Four best friends navigate loss and major life changes – and smoke a lot of weed – during their last two weeks of high scho

In [0]:
df_flags.filter((col('type')=='Movie') & (col('release_year')=='1959')).display()

duration_minutes duration_seasons type title date_added release_year rating description show_id Short_title type_flag duration_ranking is_family_friendly 143 1 Movie Ujala 10/15/2017 1959 TV An honest man dreams of a better life for his family, but a childhood friend leads him into a world of crime that keeps happiness just out of reach. 80158391 Ujala 1 57 0

In [0]:
df_flags[df_flags['release_year'].isin(['2018','2019','2020'])].groupby('release_year').count().display()

release_year count 2018 1062 2019 843 2020 25

Databricks visualization. Run in Databricks to view.

Total number of movie count over the years

In [0]:
df_years = df_flags.groupby('release_year').agg(sum((col('type') == 'Movie').cast('int')).alias('Movie'))
df_years.display()

release_year Movie 1959 1 1990 12 1975 5 1977 4 2003 35 2007 60 2018 646 1974 7 2015 358 1955 1 2006 59 1978 7 1925 0 2013 177 1942 2 1944 2 1956 1 1988 11 1997 27 1994 13 1968 3 2014 213 1973 9 1979 6 1946 2 1947 1 2019 400 1971 3 1966 1 2004 40 1991 14 1967 2 1969 2 1982 11 1945 3 1943 3 1996 14 1989 10 1998 23 1963 0 1965 2 2020 6 1985 7 1960 4 1970 1 2012 125 1987 5 2009 87 2016 592 1995 15 1980 7 2001 30 1972 3 1992 14 1958 2 1983 9 2005 51 1954 1 1984 8 2000 28 1964 1 1981 6 2010 110 1986 8 2011 100 1976 7 2008 87 2017 680 1999 17 1962 3 2002 35 1993 16

Databricks visualization. Run in Databricks to view.

Filter by Countries

In [0]:
df_countries.groupby('show_id').count().filter('count>1').display()

show_id count 80198423 2 70143865 2 80144152 4 80204402 2 70123120 2 80165848 2 70308135 2 80238080 2 80172475 2 80039136 2 80144311 2 80993655 2 81033473 2 80133117 2 80016588 4 81048916 2 80208661 2 80154179 6 80185876 2 81083590 2 81213884 2 81036061 2 80241410 2 70113636 2 70043379 4 70077546 2 70281312 2 80028732 6 80179138 2 80134695 2 80094648 4 70058024 2 80031038 2 80173002 2 80198859 2 80203786 2 80221308 2 80083752 2 80151384 2 80220311 2 70253596 8 80093103 2 80238295 2 80200015 2 81131274 2 80216146 2 70202600 10 70041162 2 80201605 2 81146370 2 80221778 6 80093812 4 80226089 4 70044256 2 60010836 2 80107987 2 70222859 2 80160081 2 80170483 2 70270745 4 80227516 2 80036140 2 80158515 2 80018987 2 80161728 2 81093951 2 81005314 2 80156939 2 81172909 2 70229046 2 70293315 8 80183187 2 60021590 2 24081514 2 80165851 2 80150002 2 80174137 2 70105599 2 81035870 2 80222951 2 80162114 2 70122316 2 81121174 2 81060049 2 80125593 2 60000393 2 80020131 2 80159877 6 80240715 4 80174897 2 80167646 4 80220541 2 80198505 2 70295169 6 70167128 2 60003540 4 70123121 2 81082327 2 80097390 4 81087762 2 80124727 2 80157564 4 81024332 2 70123160 4 80993648 2 70061763 2 80184547 2 80177416 2 80150604 2 81063160 2 70120340 4 81221913 2 81045510 2 80203792 2 80164392 2 80175913 2 80171982 4 81083791 2 80095988 2 80131479 4 70252898 6 70202589 4 80117781 2 80133042 2 70212504 4 80219119 2 80141891 4 80173269 2 510854 2 80187618 2 70291096 2 70205018 4 60022914 2 80127886 2 80122237 2 80102080 2 80227090 2 81035858 2 26009364 2 80075178 2 70293661 6 80234451 2 80176064 2 21028726 2 80108616 2 80244190 2 80098103 4 80220145 2 80163295 2 80091879 2 80141254 2 70000196 2 81028317 2 70140391 2 80162141 2 81023636 2 80994108 2 70229514 2 80221210 2 80204400 2 80049871 2 70309693 2 70304244 2 80236167 2 81013112 2 80188935 2 60033300 4 81099996 2 60033107 2 70118368 2 80211627 2 80142140 2 80164930 4 80145625 4 80218783 2 70204955 2 70104313 2 80224167 4 80997864 2 80149821 2 80161497 2 80217889 2 1151375 2 80223997 2 81168343 2 80141767 2 80988835 2 70254346 2 80117263 2 80047032 4 81096151 2 81103108 2 80233493 4 70110919 2 80134826 2 80100945 4 80103734 4 80988793 2 81121176 2 80097375 10 80191555 2 80202087 2 80178974 2 80218784 2 81036542 2 80039789 2 80040089 2 80042182 2 81002601 2 80171742 2 80202810 2 70260989 10 80227574 2 70167072 2 80107514 2 80156006 12 80997866 2 70125931 4 81025935 2 81179693 2 60000545 2 80167648 2 81057229 2 81036199 2 80213148 2 80132961 2 80223317 2 81030855 2 70074315 2 80213658 2 81121180 2 70120142 2 80117742 2 80222025 8 80165247 4 80107019 4 80017265 4 81008272 2 70197049 2 70143811 2 80116762 2 80003477 2 80994130 2 80239503 2 81017724 2 80118280 2 70243445 2 80203778 2 80081170 2 80038354 2 80158770 2 80213322 2 80183329 2 80120200 2 81121183 2 80192420 2 81054827 2 80092837 2 80190585 2 80207046 2 21302357 2 80166319 2 80057691 2 81019888 2 80068326 2 70242310 2 80175619 2 80002311 2 80040330 2 80161628 2 80128317 2 81132443 2 80241248 2 80244627 2 80156941 2 81191254 2 80028357 4 81163776 2 70100644 2 80100933 2 80186850 2 80176592 2 80038445 2 70001564 2 80135587 2 80158579 2 70218312 2 80234791 4 80191358 2 80208684 2 80100936 2 80191988 2 60001807 2 70281600 2 80168084 10 80220228 2 81045517 2 80158854 2 80238607 2 80190149 2 80122233 2 80107369 8 70157152 2 80106307 2 80039050 2 80038442 2 80095193 4 80119411 2 81196441 2 81111849 2 80120740 4 80032081 2 80117291 2 80057137 2 80223195 2 80079473 2 70245034 2 80128245 6 70299859 2 60003082 2 70084795 4 1151188 2 81044300 2 21028086 2 81150338 2 80134885 2 80189648 2 70075775 2 80173606 4 70130432 2 80094096 2 80194610 4 60020916 2 80023289 2 80213643 4 70283261 2 81004223 2 80162246 2 80201542 2 80238391 2 80059440 4 70230147 2 80117240 2 80244709 2 81048548 2 80153131 2 80216820 2 896678 2 80107989 6 80023921 2 80173711 2 80188823 2 70216819 4 70047320 2 80011846 2 80233258 2 80207879 2 80130911 2 81001809 2 81167029 2 81110383 2 81082007 6 81024

In [0]:
df_countries= df_countries.dropDuplicates(['show_id'])
df_countries.groupby('show_id').count().filter('count>1').display() 

show_id count

In [0]:
df_countriesjoin = df_flags.join(df_countries, on='show_id', how='inner')
df_countriesjoin.display()

show_id duration_minutes duration_seasons type title date_added release_year rating description Short_title type_flag duration_ranking is_family_friendly country 80988062 312 1 Movie Black Mirror: Bandersnatch 12/28/2018 2018 TV In 1984, a young programmer begins to question reality as he adapts a dark fantasy novel into a video game. A mind-bending tale with multiple endings. Black Mirror 1 1 0 United States 60002818 228 1 Movie Sangam 12/31/2019 1964 TV Returning home from war after being assumed dead, a pilot weds the woman he has long loved, unaware that she had been planning to marry his best friend. Sangam 1 2 0 India 60020906 224 1 Movie Lagaan 12/8/2017 2001 PG In 1890s India, an arrogant British commander challenges the harshly taxed residents of Champaner to a high-stakes cricket match. Lagaan 1 3 1 India 70090035 214 1 Movie Jodhaa Akbar 10/1/2018 2008 TV In 16th-century India, what begins as a strategic alliance between a Mughal emperor and a Hindu princess becomes a genuine opportunity for true love. Jodhaa Akbar 1 4 0 India 80175798 209 1 Movie The Irishman 11/27/2019 2019 R Hit man Frank Sheeran looks back at the secrets he kept as a loyal member of the Bufalino crime family in this acclaimed film from Martin Scorsese. The Irishman 1 5 0 United States 81035749 205 1 Movie The Gospel of Luke 10/19/2018 2015 TV Word-for-word Bible texts of the entire book of Luke are narrated and re-enacted in this epic production of the Gospel's accounts of Jesus's life. The Gospel of Luke 1 6 0 Morocco 70123118 203 1 Movie What's Your Raashee? 8/15/2018 2009 TV To protect his family from ruin, Yogesh must marry his dream girl in only ten days, so he rushes into dating women with different astrological signs. What's Your Raashee? 1 7 0 India 60004484 201 1 Movie The Lord of the Rings: The Return of the King 1/1/2020 2003 PG Aragorn is revealed as the heir to the ancient kings as he, Gandalf and the other members of the broken fellowship struggle to save Gondor. The Lord of the Rings 1 8 1 United States 449931 200 1 Movie Doctor Zhivago 11/1/2019 1965 PG A young physician and his beautiful mistress get swept up in the danger and drama of the Bolshevik Revolution in this Oscar-winning epic. Doctor Zhivago 1 9 1 United Kingdom 70274390 196 1 Movie Elephants Dream 4 Hour 8/23/2018 2006 TV Friends Proog and Emo live in a capricious, seemingly infinite machine with a sinister purpose in this experimental computer-animated short. Elephants Dream 4 Hour 1 10 0 Netherlands 60036359 195 1 Movie Schindler's List 4/1/2018 1993 R Oskar Schindler becomes an unlikely humanitarian, spending his entire fortune to help save 1,100 Jews from Auschwitz during World War II. Schindler's List 1 11 0 United States 60035870 193 1 Movie Hum Aapke Hain Koun 1/1/2018 1994 NR Although Nisha falls for Prem, she agrees to marry his older brother for the good of their families. But fate may have other plans for the lovebirds. Hum Aapke Hain Koun 1 12 0 India 19207412 192 1 Movie Maine Pyar Kiya 1/1/2018 1989 TV When the son of a wealthy businessman and the daughter of a struggling engineer fall in love, the young man's parents question the girl's motives. Maine Pyar Kiya 1 13 0 India 60011597 191 1 Movie Wyatt Earp 1/1/2020 1994 PG Legendary lawman Wyatt Earp is continually at odds with a gang of renegade cowboys, culminating in a fiery showdown with the outlaws at the OK Corral. Wyatt Earp 1 14 1 United States 60000440 189 1 Movie Magnolia 1/1/2020 1999 R Through chance, human action, past history and divine intervention, an eclectic cast of characters weaves and warps through each other's lives. Magnolia 1 16 0 United States 80059049 187 1 Movie Pardes 3/1/2018 1997 TV Prompted by loyalty, Arjun plays matchmaker between his philandering foster brother and a conservative girl but winds up falling in love himself. Pardes 1 17 0 India 60011729 185 1 Movie Mutiny on the Bounty 11/1/2019 1962 TV Marlon Brando gives a nuanced performance as the aristocratic Lt. Flet

In [0]:
df_countriesjoin.groupby('country').count().orderBy('count', ascending=False).limit(10).show()

+--------------+-----+
|       country|count|
+--------------+-----+
| United States|10148|
|         India| 3320|
|United Kingdom| 2352|
|        Canada| 1244|
|        France| 1080|
|         Japan|  892|
|         Spain|  704|
|   South Korea|  648|
|       Germany|  596|
|        Mexico|  512|
+--------------+-----+



In [0]:
df_flags.write.format("delta")\
    .mode("overwrite")\
    .save("abfss://gold@netflixdatalakes.dfs.core.windows.net/netflix_gold_layer")

In [0]:
df_flags.groupby('show_id').count().filter('count>1').display()


show_id count

In [0]:
df_countries.groupby('show_id').count().filter('count>1').display()

show_id count

In [0]:
df_directors.groupby('show_id').count().filter('count>1').display()

show_id count